<font size="6"><code style="background:teal;color:white">Кейс 11: А/Б тестирование</code></font>

<div class="alert alert-block alert-warning"><b>Задание:</b> Были запущены А/Б-тест на разные виды лендингов. Один короткий, на один экран, с ярким call-to-action. второй длинный, с подробным разъяснением всех плюсов нашей платформы. Тест запустили на всех незарегистрированных пользователей, заходивших на лендинг. Необходимо посмотреть с какого лендинга приходит больше людей. Какое качество (в денежном эквиваленте) этих пользователей?</div>

**Что же у нас за сервис?**  

Платформа предоставляет сервера для облачного хранения файлов. Пользователь может купить либо условно-безлимитный (до 2 ТБ данных) доступ к хранилищу на месяц за 350 рублей, на 3 месяца за 700 рублей и на год за 1500 рублей, либо купить себе пакет из 10 ГБ на год за 50 рублей.

**Где искать данные?**  

В таблице **ab_test_cookies** лежат поля cookie_id (ID куки пользователя) и grp (группа АБ-теста). 

https://drive.google.com/file/d/1veLtXyQvGwS20pwmAeGV1k1N9GST00mf/view?usp=sharing

В таблице **registrations_in_test_period** лежат регистрации пользователей за период проведения теста. Внутри 2 поля: cookie_id и user_id (ID зарегистрированного пользователя). Если пользователь зарегистрировался с лендинга АБ-теста, то поле cookie_id непустое.  

https://drive.google.com/file/d/1nH5PGGT7dSlxgUuuWC7OMd3f5zlIJnEZ/view?usp=sharing

В таблице **purchases_in_test_period** лежат платежи зарегистрированных пользователей за период проведения теста: amount — сумма покупки в рублях, user_id — ID покупателя, purchase_id — ID покупки.  

https://drive.google.com/file/d/1oWP6EtPCpWHxCi8gq8pZPPfPSkJzGt5d/view?usp=sharing

**Примечание:** не все регистрации происходят после посещения лендинга, один пользователь может совершить больше одной покупки.

**<mark>ЭТАП 1</mark>  Загружаем необходимые для работы библиотеки, сами данные, изучаем и подготавливаем их для последующего анализа.**

In [1]:
# Импорты нужных библиотек и функций
import pandas as pd
import numpy as np
from scipy import stats
from statsmodels.stats.proportion import proportion_confint
from statsmodels.stats.weightstats import ztest
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly import graph_objects as go
init_notebook_mode(connected=True)
from plotly.subplots import make_subplots

In [2]:
# Посмотрим, в каком формате предоставлены данные таблицы ab_test_groups:
ab_test_cookies = pd.read_csv('ab_test_cookies.csv')
ab_test_cookies.head()

cookie_id grp
0  65hj0vyf6kfrckx   A
1  dnjw8oy95td2jqf   B
2  beiyb0xfie92m43   B
3  xyd746tr80pnnbi   B
4  dpq6rqi93zgekgv   A

In [3]:
ab_test_cookies.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 253172 entries, 0 to 253171
Data columns (total 2 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   cookie_id  253172 non-null  object
 1   grp        253172 non-null  object
dtypes: object(2)
memory usage: 3.9+ MB


In [4]:
# Всего уникальных пользователей, которым поставили cookies
ab_test_cookies.cookie_id.nunique()

253172

In [5]:
# Количество пользователей в группах:
ab_test_cookies.groupby('grp')['cookie_id'].agg('count')

grp
A    101329
B    151843
Name: cookie_id, dtype: int64

In [6]:
# Посмотрим, как устроена таблица с регистрациями:
registrations_in_test_period = pd.read_csv('registrations_in_test_period.csv')
registrations_in_test_period.head()

cookie_id  user_id
0       NaN   382603
1       NaN   295154
2       NaN   999732
3       NaN    16486
4       NaN   678352

In [7]:
registrations_in_test_period.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 172350 entries, 0 to 172349
Data columns (total 2 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   cookie_id  72485 non-null   object
 1   user_id    172350 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 2.6+ MB


Видим, что не на всех пользователей существует информация о cookies

In [8]:
# Количество зарегистрированных пользователей, которым были оставлены cookies с тестируемого лендинга
registrations_in_test_period.cookie_id.nunique()

72485

In [9]:
# Количество зарегистрированных пользователей за интересуемый нас период
registrations_in_test_period.user_id.nunique()

172350

In [10]:
# Посмотрим, как устроена таблица платежей:
purchases_in_test_period = pd.read_csv('purchases_in_test_period.csv')
purchases_in_test_period.head()

purchase_id  user_id  amount
0            1   275851     350
1            2   923077    1500
2            3   959409      50
3            4   692022     350
4            5   737918      50

In [11]:
purchases_in_test_period.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 35147 entries, 0 to 35146
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   purchase_id  35147 non-null  int64
 1   user_id      35147 non-null  int64
 2   amount       35147 non-null  int64
dtypes: int64(3)
memory usage: 823.9 KB


In [12]:
# Посмотрим на количество уникальных покупателей
purchases_in_test_period.user_id.nunique()

33740

In [13]:
# Так как у пользователя может быть несколько покупок, нам нужно провести агрегацию по пользователю:
purchases_in_test_period = purchases_in_test_period.groupby('user_id', as_index = False).agg({'amount':'sum'})
purchases_in_test_period.head()

user_id  amount
0        0     350
1       27     700
2       33     350
3       61      50
4       76    1500

In [14]:
# Соединяем все три таблицы, чтобы получить необходимый датасет:
ab_data = ab_test_cookies.merge(registrations_in_test_period, on = 'cookie_id', how = 'left')
ab_data = ab_data.merge(purchases_in_test_period, on = 'user_id', how = 'left')
ab_data.head()

cookie_id grp   user_id  amount
0  65hj0vyf6kfrckx   A  716849.0     NaN
1  dnjw8oy95td2jqf   B       NaN     NaN
2  beiyb0xfie92m43   B       NaN     NaN
3  xyd746tr80pnnbi   B       NaN     NaN
4  dpq6rqi93zgekgv   A       NaN     NaN

**<mark>ЭТАП 2</mark>  Рассчитываем показатели.** 

In [15]:
# Посмотрим, в каких пропорциях разбиты пользователи на группы и сколько пользователей в каждой группе что-то купило:
ab_summary = ab_data.groupby('grp').agg({'cookie_id':'count', 'user_id':'count', 'amount':'count'}) #Агрегация данных
ab_summary.rename(columns={'cookie_id':'visit_users', 'user_id':'registr_users', 'amount':'buyers'}, inplace = True) 
ab_summary

visit_users  registr_users  buyers
grp                                    
A         101329          31439    5815
B         151843          41046    8797

In [16]:
# Посчитаем, какая доля пользователей находится в группе А:
ab_summary.loc[ab_summary.index == 'A', 'visit_users'].sum()/ab_summary.visit_users.sum()

0.4002377830091795

Считаем конверсию посетителей в регистрирующихся

In [17]:
ab_summary['visit_registr_conv'] = ab_summary.registr_users/ab_summary.visit_users
ab_summary

visit_users  registr_users  buyers  visit_registr_conv
grp                                                        
A         101329          31439    5815            0.310267
B         151843          41046    8797            0.270319

Считаем конверсию регистрирующихся в покупателей

In [18]:
ab_summary['registr_buyers_conv'] = ab_summary.buyers/ab_summary.registr_users
ab_summary

visit_users  registr_users  buyers  visit_registr_conv  \
grp                                                           
A         101329          31439    5815            0.310267   
B         151843          41046    8797            0.270319   

     registr_buyers_conv  
grp                       
A               0.184961  
B               0.214321

Считаем конверсию посетителей в покупателей

In [19]:
ab_summary['visit_buyers_conv'] = ab_summary.buyers/ab_summary.visit_users
ab_summary

visit_users  registr_users  buyers  visit_registr_conv  \
grp                                                           
A         101329          31439    5815            0.310267   
B         151843          41046    8797            0.270319   

     registr_buyers_conv  visit_buyers_conv  
grp                                          
A               0.184961           0.057387  
B               0.214321           0.057935

Считаем средний чек

In [20]:
ab_summary = ab_summary.merge(ab_data.groupby('grp').agg({'amount':'mean'}).rename(columns = {'amount':'avg_bill'}), 
                 left_index = True, right_index = True) # Сделали агрегацию и прикрепили её к ab_summary
ab_summary

visit_users  registr_users  buyers  visit_registr_conv  \
grp                                                           
A         101329          31439    5815            0.310267   
B         151843          41046    8797            0.270319   

     registr_buyers_conv  visit_buyers_conv    avg_bill  
grp                                                      
A               0.184961           0.057387  553.052451  
B               0.214321           0.057935  623.093100

<span style="color:teal"> <b>Очень интересный переход из посетителей в зарегистрированных, а затем и в покупателей по группам. Итоговая конверсия из визита в покупка у обоих групп практически одинаков, чего не скажешь о промежуточных этапах. Увеличение коверсии на этапе из регистрации в покупателя на 16%, как и увеличение чека в группе В на 13% свидетельствует о том, что нашей аудитории интересно предложение по данному лендингу, они видят в нем большую ценность и готовы платить больше. Но при этом у данной же группы меньше на 15% конверсия чем у группы А. Это может свидетельствовать либо о недостаточной проработке call-to-action в регистрацию, либо о нахождении на лендинге менее заинтересованной нашим продуктом аудитории.</b></span>

Считаем ARPU

Extra_revenue — выручка, которую пользователи принесли дополнительно, если считать базовой выручкой выручку всех пользователей с ARPU, равным ARPU в контрольной группе.

In [21]:
ab_summary = ab_summary.merge(ab_data.groupby('grp').agg({'amount':'sum'}).rename(columns = {'amount':'revenue'}), 
                 left_index = True, right_index = True) # Сделали агрегацию и прикрепили её к ab_summary
ab_summary['ARPU'] = ab_summary['revenue']/ab_summary.registr_users
ab_summary['Extra_revenue'] = ab_summary['registr_users']*(ab_summary['ARPU'] - ab_summary.loc['A', 'ARPU'])
pd.set_option('display.float_format', lambda x: '%.5f' % x)#избавимся от формата числа с экспонентой
ab_summary

visit_users  registr_users  buyers  visit_registr_conv  \
grp                                                           
A         101329          31439    5815             0.31027   
B         151843          41046    8797             0.27032   

     registr_buyers_conv  visit_buyers_conv  avg_bill       revenue      ARPU  \
grp                                                                             
A                0.18496            0.05739 553.05245 3216000.00000 102.29333   
B                0.21432            0.05793 623.09310 5481350.00000 133.54164   

     Extra_revenue  
grp                 
A          0.00000  
B    1282617.97926

<span style="color:teal"> <b>Согласно нашим предварительным выводам средний чек увеличился на 13%, ARPU увеличился на 31%, благодаря чему была заработана дополнительная выручка в размере 1 282 618 рублей (единицы измерения точно не даны, наше предположение).</b></span>

**<mark>ЭТАП 3</mark>  Проверяем статистическую значимость полученных результатов.**

Конверсия — бинарная величина (пользователь либо купил, либо нет), поэтому для подсчёта значимости будем использовать Z-test.  
Воспользуемся функцией statsmodels.stats.weightstats.ztest, куда нужно передать две последовательности пользовательских конверсий (то есть массивы нулей и единиц). Для этого преобразуем наши датафреймы.

In [22]:
# Использовать statsmodels.stats.weightstats.ztest, куда нужно передать две последовательности пользовательских конверсий:
ztest(ab_data.loc[ab_data.grp == 'A', 'amount'].apply(lambda x: 1 if pd.notnull(x) else 0),# Конверсии пользователей группы А
     ab_data.loc[ab_data.grp == 'B', 'amount'].apply(lambda x: 1 if pd.notnull(x) else 0) # Конверсии пользователей группы B
     ) 

(-0.5787826665981052, 0.5627358282855696)

<span style="color:teal"> <b>Z-test выдаёт два параметра: z-статистику и p-value. Нам нужно как раз p-value, которое в данном случае превышает пороговое значение 0.05, что не дает нам оснований отклонить нулевую гипотезу и признать полученные различия в конверсии статистически значимыми</b></span>

Рассмотрим теперь различия среднего чека и ARPU. Очевидно, что и средний чек, и ARPU распределены ненормально, так как у нас ограниченное количество цен на подписки. Давайте визуализируем это и проверим с помощью статистического теста Шапиро-Вилка для распределения средних чеков и покупок:

In [23]:
trace1 = go.Histogram(
            x = ab_data.loc[ab_data.grp == 'A', 'amount'].dropna(),
            name='Группа А', 
            hovertemplate="Чек: %{x} руб, <br>Количество пользователей: %{y} <extra></extra>",
            marker_color='teal',
            opacity=0.75
            )
trace2 = go.Histogram(
            x=ab_data.loc[ab_data.grp == 'B', 'amount'].dropna(),
            name='Группа В',
            hovertemplate="Чек: %{x} руб, <br>Количество пользователей: %{y} <extra></extra>",
            marker_color='salmon',
            opacity=0.75
            )

data = [trace1, trace2]

layout=go.Layout(
    title_text='Гистограмма распределения чеков на платящих пользователей ', 
    xaxis_title_text='Чек, руб', # Делаем предположение, что суммы у нас в USD,тточно не указано
    yaxis_title_text='Количество пользователей', 
    bargap=0.2, 
    bargroupgap=0.1 
)

fig=go.Figure(data = data, layout = layout)

fig.show()
print('Shapiro-Wilk p-value для группы А: ', stats.shapiro(ab_data.loc[ab_data.grp == 'A', 'amount'].dropna())[1])
print('Shapiro-Wilk p-value для группы B: ', stats.shapiro(ab_data.loc[ab_data.grp == 'B', 'amount'].dropna())[1])

Shapiro-Wilk p-value для группы А:  0.0
Shapiro-Wilk p-value для группы B:  0.0


C:\ProgramData\Anaconda3\lib\site-packages\scipy\stats\morestats.py:1676: UserWarning:

p-value may not be accurate for N > 5000.



Как видим, тест на определение нрмальности Шапиро-Вилка выдает предупреждение о недостаточной точности подсчета параметра p-value при значениях более 5000. В таких случаях рекомендуют использовать тест Колмогорова-Смирнова, но в виду графической визуалиции выше мы и так видим, что данные распределены не нормально.

In [24]:
trace1 = go.Histogram(
            x = ab_data.loc[ab_data.grp == 'A', 'amount'].fillna(0),
            name='Группа А', 
            hovertemplate="Выручка: %{x} руб, <br>Количество пользователей: %{y} <extra></extra>",
            marker_color='teal',
            opacity=0.75
            )
trace2 = go.Histogram(
            x=ab_data.loc[ab_data.grp == 'B', 'amount'].fillna(0),
            name='Группа В',
            hovertemplate="Выручка: %{x} руб, <br>Количество пользователей: %{y} <extra></extra>",
            marker_color='salmon',
            opacity=0.75
            )

data = [trace1, trace2]

layout=go.Layout(
    title_text='Гистограмма распределения выручки на пользователей ', 
    xaxis_title_text='Выручка, руб', # Делаем предположение, что суммы у нас в USD,тточно не указано
    yaxis_title_text='Количество пользователей', 
    bargap=0.2, 
    bargroupgap=0.1 
)

fig=go.Figure(data = data, layout = layout)

fig.show()
print('Shapiro-Wilk p-value для группы А: ', stats.shapiro(ab_data.loc[ab_data.grp == 'A', 'amount'].fillna(0))[1])
print('Shapiro-Wilk p-value для группы B: ', stats.shapiro(ab_data.loc[ab_data.grp == 'B', 'amount'].fillna(0))[1])

Shapiro-Wilk p-value для группы А:  0.0
Shapiro-Wilk p-value для группы B:  0.0


И визуальный анализ, и тест Шапиро-Вилка на нормальность говорят нам, что распределение не является нормальным (stats.shapiro выдаёт два числа, второе — p-value сравнения нормального распределения и нашего)

Так как распределения признаков не бинарные (0-1) и не нормальные, то нужно использовать для сравнения средних не только T-test, но и непараметрический U-тест Манна-Уитни.

U-test скажет нам, различаются ли сами распределения, а T-test покажет, различаются ли средние этих распределений. При сравнении средних величин (например, ARPU) обычно важнее показатель p-value для Т-теста. Если он меньше 0.05, а p-value теста Манна-Уитни больше 0.05, то это все равно говорит о значимых различиях показателей.

Сравниваем средние чеки

In [25]:
print(stats.mannwhitneyu(ab_data.loc[ab_data.grp == 'A', 'amount'].dropna(), ab_data.loc[ab_data.grp == 'B', 'amount'].dropna()),
stats.ttest_ind(ab_data.loc[ab_data.grp == 'A', 'amount'].dropna(), ab_data.loc[ab_data.grp == 'B', 'amount'].dropna())
      , sep = '\n')

MannwhitneyuResult(statistic=23997449.0, pvalue=1.5894355470534353e-11)
Ttest_indResult(statistic=-7.698737457881192, pvalue=1.4620086805787972e-14)


<span style="color:teal"> <b>Как мы видим, средние чеки значимо различаются (так как p-value << 0.05) по каждому из тестов.</b></span>

Сравниваем ARPU

In [26]:
print(stats.mannwhitneyu(ab_data.loc[ab_data.grp == 'A', 'amount'].fillna(0), \
                         ab_data.loc[ab_data.grp == 'B', 'amount'].fillna(0)),
      stats.ttest_ind(ab_data.loc[ab_data.grp == 'A', 'amount'].fillna(0), \
                      ab_data.loc[ab_data.grp == 'B', 'amount'].fillna(0)), sep = '\n')

MannwhitneyuResult(statistic=7687257761.0, pvalue=0.2131782418227564)
Ttest_indResult(statistic=-5.6615374023743055, pvalue=1.501844531390091e-08)


<span style="color:teal"> <b>С ARPU ситуация хуже, чем со средним чеком: хотя тест Манна-Уитни говорит, что распределения разные, Т-тест говорит, что средние этих распределений различить (с порогом p-value 0.05) нельзя. Возможно, А/Б-тест и увеличивает ARPU, но достоверно мы этого сейчас сказать не можем.</b></span>

**Строим доверительные интервалы**  
Построим для каждой метрики доверительные интервалы для среднего, чтобы визуализация была более наглядной. Это можно сделать следующим образом:

In [27]:
# Важные функции для получения доверительных интервалов
def get_conf_interval(data, conf_level = 0.95):  
# Считает доверительные интервалы для средних
        buf = (stats.t.interval(conf_level, len(data),
                             loc=np.mean(data), scale=stats.sem(data)))
        return (buf[1] - buf[0])/2
    
def get_conf_interval_z(succ, tot):  
# Считает доверительные интервалы для бинарных величин
    buf = proportion_confint(succ, tot)
    return buf[1] - buf[0]

In [28]:
# Составляем словарь с доверительными интервалами для каждой метрики и для каждой группы
conf_intervals = {'ARPU':{'A':get_conf_interval(ab_data.loc[ab_data.grp == 'A', 'amount'].fillna(0)),
                          'B':get_conf_interval(ab_data.loc[ab_data.grp == 'B', 'amount'].fillna(0))},
                  'conversion':{'A':get_conf_interval_z(ab_data.loc[ab_data.grp == 'A', 'amount'].dropna().count(),
                                                        ab_data.loc[ab_data.grp == 'A', 'user_id'].count()),
                               'B':get_conf_interval_z(ab_data.loc[ab_data.grp == 'B', 'amount'].dropna().count(),
                                                        ab_data.loc[ab_data.grp == 'B', 'user_id'].count())},
                  'avg_bill':{'A':get_conf_interval(ab_data.loc[ab_data.grp == 'A', 'amount'].dropna()),
                          'B':get_conf_interval(ab_data.loc[ab_data.grp == 'B', 'amount'].dropna())}
                 }

In [29]:
conf_intervals

{'ARPU': {'A': 1.0981455326877274, 'B': 0.9918432756035216},
 'conversion': {'A': 0.008583676140727192, 'B': 0.00793957485423974},
 'avg_bill': {'A': 13.259018604526204, 'B': 11.55088606505592}}

Итак, мы посчитали все основные метрики А/Б-теста. Пришло время подготовить по нему отчёт, который можно показать стейкхолдеру, и из которого будет видно, каких результатов мы достигли.

**<mark>ЭТАП 4</mark>  Визуализируем полученные результаты.**

In [30]:
fig = make_subplots(rows = 2, cols = 4, 
                   subplot_titles = ("users", "buyers", "conversion", "revenue", "avg_bill", "ARPU", "Extra_revenue"))

fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.visit_users,
                     name = "users",
                     text = ab_summary.visit_users,
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 1, col = 1)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.buyers,
                     name = "buyers",
                     text = ab_summary.buyers,
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 1, col = 2)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.visit_buyers_conv,
                     name = "conversion",
                     error_y = dict(type = 'data', array = [round(conf_intervals['conversion']['A'], 3), 
                                                            round(conf_intervals['conversion']['B'], 3)]),
                     text = [str(round(i*100,2))+" %" for i in ab_summary.visit_buyers_conv],
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 1, col = 3)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.revenue,
                     name = "revenue",
                     text = [str(round(i))+" р." for i in ab_summary.revenue],
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 1, col = 4)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.avg_bill,
                     name = "avg_bill",
                     error_y = dict(type = 'data', array = [round(conf_intervals['avg_bill']['A'], 3), 
                                                            round(conf_intervals['avg_bill']['B'], 3)]),
                     text = [str(round(i))+" р." for i in ab_summary.avg_bill],
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 2, col = 1)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.ARPU,
                     name = "ARPU",
                     error_y = dict(type = 'data', array = [round(conf_intervals['ARPU']['A'], 3), 
                                                            round(conf_intervals['ARPU']['B'], 3)]),
                     text = [str(round(i))+" р." for i in ab_summary.ARPU],
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 2, col = 2)
fig.add_trace(go.Bar(x = ab_summary.index, 
                     y = ab_summary.Extra_revenue,
                     name = "Extra_revenue",
                     text = [str(round(i))+" р." for i in ab_summary.Extra_revenue],
                     hovertemplate="%{x}, <br>%{y} <extra></extra>",
                     textposition='auto',
                     marker=dict(color=['teal', 'salmon'])
                    ), row = 2, col = 3)

fig.update_layout(height=500, width=980,
                  showlegend=False,
                  title_text="Результаты А/В теста на разный лендинг")
fig.show(frameon = False)

<blockquote>
<p><b>Вывод: </b>Итак, мы получили отчет по А/В тесту с интересующими нас метриками. По нему можно ответить на вопросы, связанные с метриками нашего теста с разными вариантами лендинга и сделать выводы относительно его успешности:<br><br> 1. Конверсия статистически незначимо выше на <b>1 %</b> в группе Б<br> 2. Средний чек статистически значимо выше на <b>13 %</b> в группе Б<br> 3. Значимость увеличения ARPU точно сказать нельзя, но данный показатель выше на <b>31 %</b> в группе Б <br><br><b>Рекомендации:</b> отдать предпочтение лендингу в варианте Б, изучить дополнительно конверсию перехода с посетителя в зарегистрировавшегося пользователя </p>
</blockquote>